In [1]:
import numpy as np 
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.stats import chi2_contingency 

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
app_train = pd.read_csv('/kaggle/input/home-credit-default-risk/application_train.csv')
app_test=pd.read_csv('/kaggle/input/home-credit-default-risk/application_test.csv')

In [3]:
print(app_train[['ORGANIZATION_TYPE','NAME_FAMILY_STATUS', 'CODE_GENDER']].isnull().sum())
print('-'*40)
print(app_test[['ORGANIZATION_TYPE','NAME_FAMILY_STATUS', 'CODE_GENDER']].isnull().sum())

ORGANIZATION_TYPE     0
NAME_FAMILY_STATUS    0
CODE_GENDER           0
dtype: int64
----------------------------------------
ORGANIZATION_TYPE     0
NAME_FAMILY_STATUS    0
CODE_GENDER           0
dtype: int64


In [4]:
users_nan = (app_train.isnull().sum() / app_train.shape[0]) * 100
users_nan[users_nan > 0].sort_values(ascending=False)

COMMONAREA_MEDI             69.872297
COMMONAREA_AVG              69.872297
COMMONAREA_MODE             69.872297
NONLIVINGAPARTMENTS_MEDI    69.432963
NONLIVINGAPARTMENTS_MODE    69.432963
                              ...    
EXT_SOURCE_2                 0.214626
AMT_GOODS_PRICE              0.090403
AMT_ANNUITY                  0.003902
CNT_FAM_MEMBERS              0.000650
DAYS_LAST_PHONE_CHANGE       0.000325
Length: 67, dtype: float64

In [5]:
app_train.replace({'XNA': np.nan, 'XNP': np.nan, 'Unknown': np.nan}, inplace = True)
app_test.replace({'XNA': np.nan, 'XNP': np.nan, 'Unknown': np.nan}, inplace = True)

In [6]:
print(app_train[['ORGANIZATION_TYPE','NAME_FAMILY_STATUS', 'CODE_GENDER']].isnull().sum())
print('-'*40)
print(app_test[['ORGANIZATION_TYPE','NAME_FAMILY_STATUS', 'CODE_GENDER']].isnull().sum())

ORGANIZATION_TYPE     55374
NAME_FAMILY_STATUS        2
CODE_GENDER               4
dtype: int64
----------------------------------------
ORGANIZATION_TYPE     9274
NAME_FAMILY_STATUS       0
CODE_GENDER              0
dtype: int64


In [7]:
users_nan = (app_train.isnull().sum() / app_train.shape[0]) * 100
users_nan[users_nan > 0].sort_values(ascending=False)

COMMONAREA_MODE             69.872297
COMMONAREA_MEDI             69.872297
COMMONAREA_AVG              69.872297
NONLIVINGAPARTMENTS_MODE    69.432963
NONLIVINGAPARTMENTS_MEDI    69.432963
                              ...    
AMT_ANNUITY                  0.003902
CODE_GENDER                  0.001301
CNT_FAM_MEMBERS              0.000650
NAME_FAMILY_STATUS           0.000650
DAYS_LAST_PHONE_CHANGE       0.000325
Length: 70, dtype: float64

In [8]:
app_test.drop(app_train.columns[app_train.isnull().mean()>0.4],axis=1, inplace=True)


In [9]:
app_train.drop(app_train.columns[app_train.isnull().mean()>0.4],axis=1, inplace=True)

In [10]:
app_train.shape

(307511, 73)

In [11]:
app_test.shape

(48744, 72)

In [12]:
users_nan = (app_train.isnull().sum() / app_train.shape[0]) * 100
users_nan[users_nan > 0].sort_values(ascending=False)

OCCUPATION_TYPE               31.345545
EXT_SOURCE_3                  19.825307
ORGANIZATION_TYPE             18.007161
AMT_REQ_CREDIT_BUREAU_YEAR    13.501631
AMT_REQ_CREDIT_BUREAU_QRT     13.501631
AMT_REQ_CREDIT_BUREAU_MON     13.501631
AMT_REQ_CREDIT_BUREAU_WEEK    13.501631
AMT_REQ_CREDIT_BUREAU_DAY     13.501631
AMT_REQ_CREDIT_BUREAU_HOUR    13.501631
NAME_TYPE_SUITE                0.420148
OBS_60_CNT_SOCIAL_CIRCLE       0.332021
DEF_60_CNT_SOCIAL_CIRCLE       0.332021
OBS_30_CNT_SOCIAL_CIRCLE       0.332021
DEF_30_CNT_SOCIAL_CIRCLE       0.332021
EXT_SOURCE_2                   0.214626
AMT_GOODS_PRICE                0.090403
AMT_ANNUITY                    0.003902
CODE_GENDER                    0.001301
CNT_FAM_MEMBERS                0.000650
NAME_FAMILY_STATUS             0.000650
DAYS_LAST_PHONE_CHANGE         0.000325
dtype: float64

In [13]:
users_nan = (app_test.isnull().sum() / app_test.shape[0]) * 100
users_nan[users_nan > 0].sort_values(ascending=False)

OCCUPATION_TYPE               32.014197
ORGANIZATION_TYPE             19.025931
EXT_SOURCE_3                  17.782701
AMT_REQ_CREDIT_BUREAU_HOUR    12.409732
AMT_REQ_CREDIT_BUREAU_DAY     12.409732
AMT_REQ_CREDIT_BUREAU_WEEK    12.409732
AMT_REQ_CREDIT_BUREAU_MON     12.409732
AMT_REQ_CREDIT_BUREAU_QRT     12.409732
AMT_REQ_CREDIT_BUREAU_YEAR    12.409732
NAME_TYPE_SUITE                1.868948
OBS_30_CNT_SOCIAL_CIRCLE       0.059495
DEF_30_CNT_SOCIAL_CIRCLE       0.059495
OBS_60_CNT_SOCIAL_CIRCLE       0.059495
DEF_60_CNT_SOCIAL_CIRCLE       0.059495
AMT_ANNUITY                    0.049237
EXT_SOURCE_2                   0.016412
dtype: float64

In [14]:
# Columns have less 14% NaN Values and categorical
Cat_columns_lower_percentage_nan  = [i for i in app_train.columns[(((app_train.isnull().sum() / app_train.shape[0]) * 100) > 0) 
                                                                  & (((app_train.isnull().sum() / app_train.shape[0]) * 100) < 14)] 
                                     if app_train[i].dtype == 'O']

# Columns have less 14% NaN Values and numerical
num_columns_lower_percentage_nan  = [i for i in app_train.columns[(((app_train.isnull().sum() / app_train.shape[0]) * 100) > 0) 
                                                                  & (((app_train.isnull().sum() / app_train.shape[0]) * 100) < 14)] 
                                     if app_train[i].dtype != 'O']

In [15]:
for i in Cat_columns_lower_percentage_nan:
    app_test[i].fillna(app_train[i].mode()[0], inplace=True)
    app_train[i].fillna(app_train[i].mode()[0], inplace=True)

In [16]:
col_mod_transfrom = [i for i in num_columns_lower_percentage_nan if i not in ['EXT_SOURCE_2', 'AMT_ANNUITY','AMT_GOODS_PRICE']]
col_mean_transform = ['EXT_SOURCE_2', 'AMT_ANNUITY']

In [17]:
for i in col_mod_transfrom:
    app_test[i].fillna(app_train[i].mode()[0], inplace=True)
    app_train[i].fillna(app_train[i].mode()[0], inplace=True)
for i in col_mean_transform:
    app_test[i].fillna(app_train[i].mean(), inplace=True)
    app_train[i].fillna(app_train[i].mean(), inplace=True)

In [18]:
app_train['AMT_GOODS_PRICE'].fillna(app_train['AMT_GOODS_PRICE'].median(),inplace = True)

In [19]:
all_numerical_cols = list(app_train.select_dtypes(exclude='object').columns)

cont_cols = [col for col in all_numerical_cols if col != "TARGET" and col[:5]!='FLAG_']

In [20]:
app_train[(abs(app_train['DAYS_BIRTH']) < abs(app_train['DAYS_EMPLOYED'])) & (app_train['DAYS_EMPLOYED'] != 365243)]

Empty DataFrame
Columns: [SK_ID_CURR, TARGET, NAME_CONTRACT_TYPE, CODE_GENDER, FLAG_OWN_CAR, FLAG_OWN_REALTY, CNT_CHILDREN, AMT_INCOME_TOTAL, AMT_CREDIT, AMT_ANNUITY, AMT_GOODS_PRICE, NAME_TYPE_SUITE, NAME_INCOME_TYPE, NAME_EDUCATION_TYPE, NAME_FAMILY_STATUS, NAME_HOUSING_TYPE, REGION_POPULATION_RELATIVE, DAYS_BIRTH, DAYS_EMPLOYED, DAYS_REGISTRATION, DAYS_ID_PUBLISH, FLAG_MOBIL, FLAG_EMP_PHONE, FLAG_WORK_PHONE, FLAG_CONT_MOBILE, FLAG_PHONE, FLAG_EMAIL, OCCUPATION_TYPE, CNT_FAM_MEMBERS, REGION_RATING_CLIENT, REGION_RATING_CLIENT_W_CITY, WEEKDAY_APPR_PROCESS_START, HOUR_APPR_PROCESS_START, REG_REGION_NOT_LIVE_REGION, REG_REGION_NOT_WORK_REGION, LIVE_REGION_NOT_WORK_REGION, REG_CITY_NOT_LIVE_CITY, REG_CITY_NOT_WORK_CITY, LIVE_CITY_NOT_WORK_CITY, ORGANIZATION_TYPE, EXT_SOURCE_2, EXT_SOURCE_3, OBS_30_CNT_SOCIAL_CIRCLE, DEF_30_CNT_SOCIAL_CIRCLE, OBS_60_CNT_SOCIAL_CIRCLE, DEF_60_CNT_SOCIAL_CIRCLE, DAYS_LAST_PHONE_CHANGE, FLAG_DOCUMENT_2, FLAG_DOCUMENT_3, FLAG_DOCUMENT_4, FLAG_DOCUMENT_5, FLAG_DOCUMENT_6, FLAG_DOCUMENT_7, FLAG_DOCUMENT_8, FLAG_DOCUMENT_9, FLAG_DOCUMENT_10, FLAG_DOCUMENT_11, FLAG_DOCUMENT_12, FLAG_DOCUMENT_13, FLAG_DOCUMENT_14, FLAG_DOCUMENT_15, FLAG_DOCUMENT_16, FLAG_DOCUMENT_17, FLAG_DOCUMENT_18, FLAG_DOCUMENT_19, FLAG_DOCUMENT_20, FLAG_DOCUMENT_21, AMT_REQ_CREDIT_BUREAU_HOUR, AMT_REQ_CREDIT_BUREAU_DAY, AMT_REQ_CREDIT_BUREAU_WEEK, AMT_REQ_CREDIT_BUREAU_MON, AMT_REQ_CREDIT_BUREAU_QRT, AMT_REQ_CREDIT_BUREAU_YEAR]
Index: []

[0 rows x 73 columns]

In [21]:
proper_days_empolyed_df = app_train
proper_days_empolyed_df['YEARS_EMPLOYED'] = proper_days_empolyed_df['DAYS_EMPLOYED']/-365.25


In [22]:
app_train['DAYS_EMPLOYED'].replace({365243:np.nan},inplace=True) 
app_test['DAYS_EMPLOYED'].replace({365243:np.nan},inplace=True) 

In [23]:
proper_days_empolyed_df = app_train
proper_days_empolyed_df['YEARS_EMPLOYED'] = proper_days_empolyed_df['DAYS_EMPLOYED']/-365.25


In [24]:
app_train.groupby(['OCCUPATION_TYPE'])['DAYS_EMPLOYED'].mean()

OCCUPATION_TYPE
Accountants             -2394.102823
Cleaning staff          -2131.155665
Cooking staff           -2152.466868
Core staff              -2797.755967
Drivers                 -1939.034618
HR staff                -2278.866785
High skill tech staff   -2739.979086
IT staff                -2095.570342
Laborers                -2424.143152
Low-skill Laborers      -1664.186813
Managers                -2759.318937
Medicine staff          -3750.265550
Private service staff   -2238.281297
Realty agents           -1785.003995
Sales staff             -1703.789421
Secretaries             -2607.050575
Security staff          -1904.809106
Waiters/barmen staff    -1873.172849
Name: DAYS_EMPLOYED, dtype: float64

In [25]:
## create dataframe with total income > 1M
susp_df1 = app_train[app_train['AMT_INCOME_TOTAL']>1e+6][['AMT_INCOME_TOTAL','AMT_CREDIT','AMT_ANNUITY','CNT_CHILDREN', 'TARGET']].sort_values(by='AMT_INCOME_TOTAL', ascending=False)

## create Credit/Income and Annuity/Income percentages
susp_df1['Credit/Income'] = susp_df1['AMT_CREDIT']/susp_df1['AMT_INCOME_TOTAL']
susp_df1['Annuity/Income'] = susp_df1['AMT_ANNUITY']/susp_df1['AMT_INCOME_TOTAL']

## show only clients with difficuties
susp_df1[susp_df1['TARGET']==1].sort_values(by='Credit/Income', ascending=True)

AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  CNT_CHILDREN  TARGET  \
12840        117000000.0    562491.0      26194.5             1       1   
248159         3150000.0    900000.0      48825.0             1       1   
151018         1080000.0    371245.5      17437.5             0       1   
167656         1575000.0    553806.0      28273.5             0       1   
173663         1350000.0    491211.0      50463.0             3       1   
41725          1890000.0    781920.0      61906.5             1       1   
234728         1350000.0    576072.0      28017.0             0       1   
248970         1890000.0    900000.0      57649.5             0       1   
265884         1170000.0    983299.5      41661.0             1       1   
234861         1260000.0   1097491.5      46629.0             0       1   
38271          1125000.0   1006920.0      40063.5             0       1   
102626         1305000.0   1339884.0      39307.5             0       1   
196106         1350000.0   2517300.0      93420.0             2       1   

        Credit/Income  Annuity/Income  
12840        0.004808        0.000224  
248159       0.285714        0.015500  
151018       0.343746        0.016146  
167656       0.351623        0.017951  
173663       0.363860        0.037380  
41725        0.413714        0.032755  
234728       0.426720        0.020753  
248970       0.476190        0.030502  
265884       0.840427        0.035608  
234861       0.871025        0.037007  
38271        0.895040        0.035612  
102626       1.026731        0.030121  
196106       1.864667        0.069200

In [26]:
app_train = app_train[app_train['AMT_INCOME_TOTAL'] != 117000000.0]


In [27]:
## extract dataframe with DAYS_BIRTH and TARGET only
susp_df2 = app_train[['DAYS_BIRTH','TARGET']]

## create column represnts the age in years
susp_df2['YEARS_BIRTH'] = np.abs(susp_df2['DAYS_BIRTH']) / 365.25

## show datafame
display(susp_df2.sort_values(by='YEARS_BIRTH', ascending=False))

## show the value counts of those who are aged > 65 with respect to target
display(susp_df2[(susp_df2['YEARS_BIRTH']>65)]['TARGET'].value_counts())

/tmp/ipykernel_34/200317661.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  susp_df2['YEARS_BIRTH'] = np.abs(susp_df2['DAYS_BIRTH']) / 365.25


DAYS_BIRTH  TARGET  YEARS_BIRTH
265026      -25229       0    69.073238
63316       -25201       0    68.996578
124430      -25201       0    68.996578
143266      -25200       0    68.993840
130108      -25197       0    68.985626
...            ...     ...          ...
220805       -7678       1    21.021218
170384       -7676       0    21.015743
53702        -7676       0    21.015743
168135       -7673       0    21.007529
235444       -7489       0    20.503765

[307510 rows x 3 columns]

0    7588
1     288
Name: TARGET, dtype: int64

In [28]:
cat_col = app_train.select_dtypes('object')
cat_col.describe()

NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY  \
count              307510      307510       307510          307510   
unique                  2           2            2               2   
top            Cash loans           F            N               Y   
freq               278231      202451       202923          213311   

       NAME_TYPE_SUITE NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
count           307510           307510                         307510   
unique               7                8                              5   
top      Unaccompanied          Working  Secondary / secondary special   
freq            249817           158773                         218390   

       NAME_FAMILY_STATUS  NAME_HOUSING_TYPE OCCUPATION_TYPE  \
count              307510             307510          211119   
unique                  5                  6              18   
top               Married  House / apartment        Laborers   
freq               196433             272867           55185   

       WEEKDAY_APPR_PROCESS_START       ORGANIZATION_TYPE  
count                      307510                  252136  
unique                          7                      57  
top                       TUESDAY  Business Entity Type 3  
freq                        53900                   67991

In [29]:
app_train.groupby(['NAME_EDUCATION_TYPE'])['OCCUPATION_TYPE'].agg(pd.Series.mode)


NAME_EDUCATION_TYPE
Academic degree                    Managers
Higher education                 Core staff
Incomplete higher                  Laborers
Lower secondary                    Laborers
Secondary / secondary special      Laborers
Name: OCCUPATION_TYPE, dtype: object

In [30]:
app_train['OCCUPATION_TYPE'].isnull().sum()
app_test['OCCUPATION_TYPE'].isnull().sum()

15605

In [31]:
app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Secondary / secondary special'] = app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Secondary / secondary special'].fillna('Laborers')
app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Higher education'] =  app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Higher education'].fillna('Core staff')
app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Incomplete higher'] = app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Incomplete higher'].fillna('Laborers')
app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Lower secondary'] = app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Lower secondary'].fillna('Laborers')
app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Academic degree'] = app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Academic degree'].fillna('Managers')

app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Secondary / secondary special'] = app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Secondary / secondary special'].fillna('Laborers')
app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Higher education'] =  app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Higher education'].fillna('Core staff')
app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Incomplete higher'] = app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Incomplete higher'].fillna('Laborers')
app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Lower secondary'] = app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Lower secondary'].fillna('Laborers')
app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Academic degree'] = app_test['OCCUPATION_TYPE'][app_test['NAME_EDUCATION_TYPE']=='Academic degree'].fillna('Managers')

/tmp/ipykernel_34/1817237716.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Secondary / secondary special'] = app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Secondary / secondary special'].fillna('Laborers')
/tmp/ipykernel_34/1817237716.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Secondary / secondary special'] = app_train['OCCUPATION_TYPE'][app_train['NAME_EDUCATION_TYPE']=='Secondary / secondary special'].fillna('Laborers')
/tmp/ipykernel_34/1817237716.py:2: Set

In [32]:
app_train.groupby(['OCCUPATION_TYPE'])['ORGANIZATION_TYPE'].agg(pd.Series.mode)

OCCUPATION_TYPE
Accountants              Business Entity Type 3
Cleaning staff           Business Entity Type 3
Cooking staff            Business Entity Type 3
Core staff               Business Entity Type 3
Drivers                  Business Entity Type 3
HR staff                 Business Entity Type 3
High skill tech staff    Business Entity Type 3
IT staff                 Business Entity Type 3
Laborers                 Business Entity Type 3
Low-skill Laborers       Business Entity Type 3
Managers                 Business Entity Type 3
Medicine staff                         Medicine
Private service staff             Self-employed
Realty agents                     Self-employed
Sales staff                       Self-employed
Secretaries                            Medicine
Security staff                         Security
Waiters/barmen staff     Business Entity Type 3
Name: ORGANIZATION_TYPE, dtype: object

In [33]:
app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Accountants') |
                               (app_train['OCCUPATION_TYPE'] == 'Cleaning staff') |
                               (app_train['OCCUPATION_TYPE'] == 'Cooking staff') |
                               (app_train['OCCUPATION_TYPE'] == 'Core staff')|
                               (app_train['OCCUPATION_TYPE'] == 'Drivers')|
                               (app_train['OCCUPATION_TYPE'] == 'HR staff')|
                               (app_train['OCCUPATION_TYPE'] == 'High skill tech staff')|
                               (app_train['OCCUPATION_TYPE'] == 'IT staff')|
                               (app_train['OCCUPATION_TYPE'] == 'Laborers')|
                               (app_train['OCCUPATION_TYPE'] == 'Low-skill Laborers')|
                               (app_train['OCCUPATION_TYPE'] == 'Managers')] = app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Accountants') |
                               (app_train['OCCUPATION_TYPE'] == 'Cleaning staff') |
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'Cooking staff') |
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'Core staff')|
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'Drivers')|
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'HR staff')|
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'High skill tech staff')|
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'IT staff')|
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'Laborers')|
                                                                                                             (app_train['OCCUPATION_TYPE'] == 'Low-skill Laborers')|
                                                                                                              (app_train['OCCUPATION_TYPE'] == 'Managers')].fillna('Business Entity Type 3')

app_test['ORGANIZATION_TYPE'][(app_test['OCCUPATION_TYPE'] == 'Accountants') |
                               (app_test['OCCUPATION_TYPE'] == 'Cleaning staff') |
                               (app_test['OCCUPATION_TYPE'] == 'Cooking staff') |
                               (app_test['OCCUPATION_TYPE'] == 'Core staff')|
                               (app_test['OCCUPATION_TYPE'] == 'Drivers')|
                               (app_test['OCCUPATION_TYPE'] == 'HR staff')|
                               (app_test['OCCUPATION_TYPE'] == 'High skill tech staff')|
                              (app_test['OCCUPATION_TYPE'] == 'IT staff')|
                               (app_test['OCCUPATION_TYPE'] == 'Laborers')|
                               (app_test['OCCUPATION_TYPE'] == 'Low-skill Laborers')|
                               (app_test['OCCUPATION_TYPE'] == 'Managers')] = app_test['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Accountants') |
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'Cleaning staff') |
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'Cooking staff') |
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'Core staff')|
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'Drivers')|
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'HR staff')|
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'High skill tech staff')|
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'IT staff')|
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'Laborers')|
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'Low-skill Laborers')|
                                                                                                            (app_test['OCCUPATION_TYPE'] == 'Managers')].fillna('Business Entity Type 3')


app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Medicine staff')|
                              (app_train['OCCUPATION_TYPE'] == 'Secretaries')] = app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Medicine staff')|
                                                                                                                  (app_train['OCCUPATION_TYPE'] == 'Secretaries')].fillna('Medicine')
app_test['ORGANIZATION_TYPE'][(app_test['OCCUPATION_TYPE'] == 'Medicine staff')|
                              (app_test['OCCUPATION_TYPE'] == 'Secretaries')] = app_test['ORGANIZATION_TYPE'][(app_test['OCCUPATION_TYPE'] == 'Medicine staff')|
                                                                                                                  (app_test['OCCUPATION_TYPE'] == 'Secretaries')].fillna('Medicine')
app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Private service staff')|
                               (app_train['OCCUPATION_TYPE'] == 'Realty agents')|
                               (app_train['OCCUPATION_TYPE'] == 'Sales staff')] = app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Private service staff')|
                             (app_train['OCCUPATION_TYPE'] == 'Realty agents')|
                                                                                                                 (app_train['OCCUPATION_TYPE'] == 'Sales staff')].fillna('Self-employed')
app_test['ORGANIZATION_TYPE'][(app_test['OCCUPATION_TYPE'] == 'Private service staff')|
                               (app_test['OCCUPATION_TYPE'] == 'Realty agents')|
                               (app_test['OCCUPATION_TYPE'] == 'Sales staff')] = app_test['ORGANIZATION_TYPE'][(app_test['OCCUPATION_TYPE'] == 'Private service staff')|
                                                                                                                 (app_test['OCCUPATION_TYPE'] == 'Realty agents')|
                                                                                                                 (app_test['OCCUPATION_TYPE'] == 'Sales staff')].fillna('Self-employed')

app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Security staff')] = app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Security staff')].fillna('Security')
app_test['ORGANIZATION_TYPE'][(app_test['OCCUPATION_TYPE'] == 'Security staff')] = app_test['ORGANIZATION_TYPE'][(app_test['OCCUPATION_TYPE'] == 'Security staff')].fillna('Security')


/tmp/ipykernel_34/1284962101.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Accountants') |
/tmp/ipykernel_34/1284962101.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app_train['ORGANIZATION_TYPE'][(app_train['OCCUPATION_TYPE'] == 'Accountants') |
/tmp/ipykernel_34/1284962101.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app_test['ORGANIZATION_TYPE'][(ap

In [34]:
app_test['ORGANIZATION_TYPE'] = app_test['ORGANIZATION_TYPE'].fillna(app_test['ORGANIZATION_TYPE'].mode()[0])

In [35]:
app_test['EXT_SOURCE_3'] = app_test['EXT_SOURCE_3'].fillna(app_train.groupby(['OCCUPATION_TYPE'])['EXT_SOURCE_3'].transform('mean'))
app_train['EXT_SOURCE_3'] = app_train['EXT_SOURCE_3'].fillna(app_train.groupby(['OCCUPATION_TYPE'])['EXT_SOURCE_3'].transform('mean'))

/tmp/ipykernel_34/1368104461.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app_train['EXT_SOURCE_3'] = app_train['EXT_SOURCE_3'].fillna(app_train.groupby(['OCCUPATION_TYPE'])['EXT_SOURCE_3'].transform('mean'))


In [36]:
app_test['DAYS_EMPLOYED'] = app_test['DAYS_EMPLOYED'].fillna(app_train.groupby(['OCCUPATION_TYPE'])['DAYS_EMPLOYED'].transform('mean'))
app_train['DAYS_EMPLOYED'] = app_train['DAYS_EMPLOYED'].fillna(app_train.groupby(['OCCUPATION_TYPE'])['DAYS_EMPLOYED'].transform('mean'))

/tmp/ipykernel_34/1216194966.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app_train['DAYS_EMPLOYED'] = app_train['DAYS_EMPLOYED'].fillna(app_train.groupby(['OCCUPATION_TYPE'])['DAYS_EMPLOYED'].transform('mean'))


In [37]:
proper_days_empolyed_df = app_train
proper_days_empolyed_df['YEARS_EMPLOYED'] = proper_days_empolyed_df['DAYS_EMPLOYED']/-365.25

In [38]:
app_test['NAME_TYPE_SUITE'].replace({'Other_A':'Other','Other_B':'Other','Group of people':'Other'},inplace=True)
app_train['NAME_TYPE_SUITE'].replace({'Other_A':'Other','Other_B':'Other','Group of people':'Other'},inplace=True)

app_test['NAME_INCOME_TYPE'].replace({'Unemployed':'Other','Student':'Other','Maternity leave':'Other'},inplace=True)
app_train['NAME_INCOME_TYPE'].replace({'Unemployed':'Other','Student':'Other','Maternity leave':'Other'},inplace=True)

In [39]:
app_train['ORGANIZATION_TYPE'].value_counts(normalize = True)

Business Entity Type 3    0.401174
Self-employed             0.124913
Other                     0.054252
Medicine                  0.036399
Business Entity Type 2    0.034318
Government                0.033833
School                    0.028919
Trade: type 7             0.025466
Kindergarten              0.022373
Construction              0.021856
Business Entity Type 1    0.019460
Transport: type 4         0.017554
Trade: type 3             0.011356
Industry: type 9          0.010952
Industry: type 3          0.010660
Security                  0.010559
Housing                   0.009619
Industry: type 11         0.008793
Military                  0.008566
Bank                      0.008153
Agriculture               0.007980
Police                    0.007613
Transport: type 2         0.007167
Postal                    0.007014
Security Ministries       0.006419
Trade: type 2             0.006179
Restaurant                0.005889
Services                  0.005122
University          

In [40]:
others = app_train['ORGANIZATION_TYPE'].value_counts().index[15:]
label = 'Others'
app_train['ORGANIZATION_TYPE'] = app_train['ORGANIZATION_TYPE'].replace(others, label)
app_test['ORGANIZATION_TYPE'] = app_test['ORGANIZATION_TYPE'].replace(others, label)

In [41]:
app_train['ORGANIZATION_TYPE'].unique()


array(['Business Entity Type 3', 'School', 'Government', 'Others',
       'Other', 'Medicine', 'Business Entity Type 2', 'Self-employed',
       'Construction', 'Kindergarten', 'Trade: type 7',
       'Transport: type 4', 'Business Entity Type 1', 'Trade: type 3',
       'Industry: type 3', 'Industry: type 9'], dtype=object)

In [42]:
users_nan = (app_train.isnull().sum() / app_train.shape[0]) * 100
users_nan[users_nan > 0].sort_values(ascending=False)

Series([], dtype: float64)

In [43]:
users_nan = (app_test.isnull().sum() / app_test.shape[0]) * 100
users_nan[users_nan > 0].sort_values(ascending=False)

Series([], dtype: float64)

In [44]:
app_train.drop(['YEARS_EMPLOYED'], axis = 1,inplace=True)


In [45]:
print(app_train['TARGET'].isnull().sum())


0


In [46]:
app_train = app_train.drop(columns=['CNT_FAM_MEMBERS','LIVE_REGION_NOT_WORK_REGION', 'REG_REGION_NOT_WORK_REGION', 'OBS_60_CNT_SOCIAL_CIRCLE'])
app_test = app_test.drop(columns=['CNT_FAM_MEMBERS','LIVE_REGION_NOT_WORK_REGION', 'REG_REGION_NOT_WORK_REGION', 'OBS_60_CNT_SOCIAL_CIRCLE'])

In [47]:
cols_to_remove = ['AMT_CREDIT', 'CNT_FAM_MEMBERS', 'REG_REGION_NOT_WORK_REGION', 'LIVE_REGION_NOT_WORK_REGION', 'OBS_60_CNT_SOCIAL_CIRCLE','SK_ID_CURR']
cont_cols = list(set(cont_cols) - set(cols_to_remove))
cont_cols 

['REGION_RATING_CLIENT',
 'AMT_GOODS_PRICE',
 'OBS_30_CNT_SOCIAL_CIRCLE',
 'AMT_REQ_CREDIT_BUREAU_QRT',
 'AMT_REQ_CREDIT_BUREAU_YEAR',
 'DEF_60_CNT_SOCIAL_CIRCLE',
 'REGION_RATING_CLIENT_W_CITY',
 'DEF_30_CNT_SOCIAL_CIRCLE',
 'REGION_POPULATION_RELATIVE',
 'AMT_REQ_CREDIT_BUREAU_DAY',
 'AMT_ANNUITY',
 'DAYS_BIRTH',
 'DAYS_REGISTRATION',
 'EXT_SOURCE_3',
 'DAYS_EMPLOYED',
 'AMT_REQ_CREDIT_BUREAU_WEEK',
 'REG_CITY_NOT_LIVE_CITY',
 'DAYS_ID_PUBLISH',
 'AMT_REQ_CREDIT_BUREAU_HOUR',
 'AMT_INCOME_TOTAL',
 'AMT_REQ_CREDIT_BUREAU_MON',
 'DAYS_LAST_PHONE_CHANGE',
 'EXT_SOURCE_2',
 'REG_REGION_NOT_LIVE_REGION',
 'REG_CITY_NOT_WORK_CITY',
 'LIVE_CITY_NOT_WORK_CITY',
 'CNT_CHILDREN',
 'HOUR_APPR_PROCESS_START']

In [48]:
#Для этого использовался метод межквартильного размаха (IQR), который вычисляет разницу между 75-м и 25-м процентилями значений столбца. 
#Затем значения, выходящие за пределы диапазона от Q1-1.5IQR до Q3+1.5IQR, были заменены на медианные значения. 
#Это позволило удалить выбросы, которые могли бы исказить результаты анализа
def impute_outliers_IQR(df):

    q1=df.quantile(0.25)
    q3=df.quantile(0.75)

    IQR=q3-q1

    upper = df[~(df>(q3+1.5*IQR))].max()
    lower = df[~(df<(q1-1.5*IQR))].min()

    df = np.where(df > upper, df.quantile(0.8), np.where(df < lower, df.quantile(0.2),df))

    return df

In [49]:
for i in cont_cols:
    app_train[i] = impute_outliers_IQR(app_train[i])
    app_test[i] = impute_outliers_IQR(app_test[i])

In [50]:
app_train['LTV'] = app_train['AMT_CREDIT']/app_train['AMT_GOODS_PRICE']
app_train['DTI'] = app_train['AMT_ANNUITY']/app_train['AMT_INCOME_TOTAL']
app_train['Employed/Birth'] = app_train['DAYS_EMPLOYED']/app_train['DAYS_BIRTH'] 
app_train['Flag_Greater_30'] = (app_train['DAYS_BIRTH']/-365.25).apply(lambda x: 1 if x > 30 else 0)
app_train['Flag_Employment_Greater_5'] = (app_train['DAYS_EMPLOYED']/-365.25).apply(lambda x: 1 if x > 5 else 0)

app_test['LTV'] = app_test['AMT_CREDIT']/app_test['AMT_GOODS_PRICE']
app_test['DTI'] = app_test['AMT_ANNUITY']/app_test['AMT_INCOME_TOTAL']
app_test['Employed/Birth'] = app_test['DAYS_EMPLOYED']/app_test['DAYS_BIRTH']
app_test['Flag_Greater_30'] = (app_test['DAYS_BIRTH']/-365.25).apply(lambda x: 1 if x > 30 else 0)
app_test['Flag_Employment_Greater_5'] = (app_test['DAYS_EMPLOYED']/-365.25).apply(lambda x: 1 if x > 5 else 0)

In [51]:
# for pre-processing

from sklearn.preprocessing import OrdinalEncoder
from category_encoders import TargetEncoder 
from sklearn.model_selection import train_test_split, GridSearchCV, RandomizedSearchCV

# for machine learning modelling
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier
from sklearn.metrics import roc_auc_score, confusion_matrix

In [52]:
app_train[cat_col.columns]


NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY  \
0              Cash loans           M            N               Y   
1              Cash loans           F            N               N   
2         Revolving loans           M            Y               Y   
3              Cash loans           F            N               Y   
4              Cash loans           M            N               Y   
...                   ...         ...          ...             ...   
307506         Cash loans           M            N               N   
307507         Cash loans           F            N               Y   
307508         Cash loans           F            N               Y   
307509         Cash loans           F            N               Y   
307510         Cash loans           F            N               N   

       NAME_TYPE_SUITE      NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
0        Unaccompanied               Working  Secondary / secondary special   
1               Family         State servant               Higher education   
2        Unaccompanied               Working  Secondary / secondary special   
3        Unaccompanied               Working  Secondary / secondary special   
4        Unaccompanied               Working  Secondary / secondary special   
...                ...                   ...                            ...   
307506   Unaccompanied               Working  Secondary / secondary special   
307507   Unaccompanied             Pensioner  Secondary / secondary special   
307508   Unaccompanied               Working               Higher education   
307509   Unaccompanied  Commercial associate  Secondary / secondary special   
307510   Unaccompanied  Commercial associate               Higher education   

          NAME_FAMILY_STATUS  NAME_HOUSING_TYPE OCCUPATION_TYPE  \
0       Single / not married  House / apartment        Laborers   
1                    Married  House / apartment      Core staff   
2       Single / not married  House / apartment        Laborers   
3             Civil marriage  House / apartment        Laborers   
4       Single / not married  House / apartment      Core staff   
...                      ...                ...             ...   
307506             Separated       With parents     Sales staff   
307507                 Widow  House / apartment        Laborers   
307508             Separated  House / apartment        Managers   
307509               Married  House / apartment        Laborers   
307510               Married  House / apartment        Laborers   

       WEEKDAY_APPR_PROCESS_START       ORGANIZATION_TYPE  
0                       WEDNESDAY  Business Entity Type 3  
1                          MONDAY                  School  
2                          MONDAY              Government  
3                       WEDNESDAY  Business Entity Type 3  
4                        THURSDAY                  Others  
...                           ...                     ...  
307506                   THURSDAY                  Others  
307507                     MONDAY  Business Entity Type 3  
307508                   THURSDAY                  School  
307509                  WEDNESDAY  Business Entity Type 1  
307510                   THURSDAY  Business Entity Type 3  

[307510 rows x 12 columns]

In [53]:
enc = TargetEncoder()
app_train[cat_col.columns] = enc.fit_transform(app_train[cat_col.columns], app_train['TARGET'])

In [54]:
app_test[cat_col.columns] = enc.transform(app_test[cat_col.columns])

In [55]:
X = app_train.drop(columns=['TARGET','SK_ID_CURR'])
y = app_train['TARGET']

In [56]:
X_train, X_val, y_train, y_val = train_test_split(X, y, train_size=0.8, stratify=y, random_state=42)

In [57]:
# create a function for trained models evaluation
def evaluate_model(model):
    # prediction
    train_pred = model.predict(X_train)
    test_pred = model.predict(X_val)
    
    train_pred_proba = model.predict_proba(X_train)
    test_pred_proba = model.predict_proba(X_val)
    
    # evaluations
    print('Training & Validation ROC AUC Scores:\n', '-'*40)
    print('Training   roc auc score= {:.4f}'.format(roc_auc_score(y_train, train_pred_proba[:, 1])))
    print('Validation roc auc score= {:.4f}'.format(roc_auc_score(y_val, test_pred_proba[:, 1])))
    print('')
    print('Training & Validation Confusion Metrices:')
    print('Training   confusion matrix:\n', confusion_matrix(y_train, train_pred))
    print('Validation confusion matrix:\n', confusion_matrix(y_val, test_pred))

In [58]:
#В этом коде мы импортируем модуль RandomForestClassifier из библиотеки sklearn.ensemble и создаем объект модели rf. 
#Затем мы обучаем модель на тренировочных данных с помощью метода fit. 
#После этого мы используем модель для предсказания классов на тестовых данных с помощью метода predict. 
#Наконец, мы оцениваем качество модели на тестовых данных с помощью метрик classification_report и confusion_matrix из библиотеки sklearn.metrics.
rf = RandomForestClassifier(n_estimators=70, max_depth=15, random_state=42)
rf2 = RandomForestClassifier(n_estimators=100, max_depth=15, random_state=5)
rf3 = RandomForestClassifier(n_estimators=75, max_depth=15, random_state=30)
rf4 = RandomForestClassifier(n_estimators=80, max_depth=15, random_state=4)
rf5 = RandomForestClassifier(n_estimators=110, max_depth=15, random_state=12)

In [59]:
rf.fit(X_train, y_train)


RandomForestClassifier(max_depth=15, n_estimators=70, random_state=42)

In [60]:
evaluate_model(rf)


Training & Validation ROC AUC Scores:
 ----------------------------------------
Training   roc auc score= 0.9599
Validation roc auc score= 0.7316

Training & Validation Confusion Metrices:
Training   confusion matrix:
 [[226149      0]
 [ 19299    560]]
Validation confusion matrix:
 [[56537     0]
 [ 4964     1]]


In [61]:
rf.fit(X_train, y_train)
rf2.fit(X_train, y_train)
rf3.fit(X_train, y_train)
rf4.fit(X_train, y_train)
rf5.fit(X_train, y_train)

RandomForestClassifier(max_depth=15, n_estimators=110, random_state=12)

In [62]:
y_pred = rf.predict_proba(X_val)
y_pred2 = rf2.predict_proba(X_val)
y_pred3 = rf3.predict_proba(X_val)
y_pred4 = rf4.predict_proba(X_val)
y_pred5 = rf5.predict_proba(X_val)

y_final = (y_pred+y_pred2+y_pred3+y_pred4+y_pred5)/5

In [63]:
roc_auc_score(y_val,y_final[:, 1])

0.737333643907159

In [64]:
#была обнаружена проблема несбалансированных классов в задаче бинарной классификации. В данных было намного больше объектов с положительным классом (клиенты, вернувшие кредит вовремя) по сравнению с отрицательным классом (клиенты, не вернувшие кредит вовремя).
#В данном проекте параметр class_weight был установлен в значение "balanced". Это значение автоматически вычисляет веса классов, основываясь на их соотношении в данных, и присваивает больший вес редкому классу. 
param_grid = {'criterion' : ['gini'],
             'class_weight' : ['balanced_subsample','balanced',None],
             'max_features' : ['sqrt', 'log2']}

rf2 = RandomForestClassifier(n_estimators=100, max_depth=15, random_state=42)

grid_cv = RandomizedSearchCV(rf2,param_grid, cv=5,  scoring = 'roc_auc')

grid_cv.fit(X_train, y_train)

y_pred = grid_cv.predict_proba(X_val)

/opt/conda/lib/python3.10/site-packages/sklearn/model_selection/_search.py:305: UserWarning: The total space of parameters 6 is smaller than n_iter=10. Running 6 iterations. For exhaustive searches, use GridSearchCV.
  warnings.warn(


In [65]:
roc_auc_score(y_val, y_pred[:, 1])


0.7325700726850695

In [66]:
grid_cv.best_params_ 

{'max_features': 'sqrt', 'criterion': 'gini', 'class_weight': None}

In [67]:
rf = RandomForestClassifier(max_features= 'sqrt', criterion ='gini', n_estimators=70, max_depth=15, random_state=42)
rf2 = RandomForestClassifier(max_features= 'sqrt', criterion ='gini',n_estimators=100, max_depth=15, random_state=5)
rf3 = RandomForestClassifier(max_features= 'sqrt', criterion ='gini', n_estimators=75, max_depth=15, random_state=30)
rf4 = RandomForestClassifier(max_features= 'sqrt', criterion ='gini', n_estimators=80, max_depth=15, random_state=4)
rf5 = RandomForestClassifier(max_features= 'sqrt', criterion ='gini', n_estimators=100, max_depth=15, random_state=12)

In [68]:
rf.fit(X_train, y_train)
rf2.fit(X_train, y_train)
rf3.fit(X_train, y_train)
rf4.fit(X_train, y_train)
rf5.fit(X_train, y_train)

RandomForestClassifier(max_depth=15, random_state=12)

In [69]:
y_pred = rf.predict_proba(X_val)
y_pred2 = rf2.predict_proba(X_val)
y_pred3 = rf3.predict_proba(X_val)
y_pred4 = rf4.predict_proba(X_val)
y_pred5 = rf5.predict_proba(X_val)

y_final = (y_pred+y_pred2+y_pred3+y_pred4+y_pred5)/5

In [70]:
roc_auc_score(y_val, y_final[:, 1])


0.7373858052051254

In [71]:
test_set_dropID = app_test.drop(columns=['SK_ID_CURR'])

y_pred = rf.predict_proba(test_set_dropID)
y_pred2 = rf2.predict_proba(test_set_dropID)
y_pred3 = rf3.predict_proba(test_set_dropID)
y_pred4 = rf4.predict_proba(test_set_dropID)
y_pred5 = rf5.predict_proba(test_set_dropID)

test_proba = (y_pred+y_pred2+y_pred3+y_pred4+y_pred5)/5

test_proba

array([[0.9079806 , 0.0920194 ],
       [0.86266915, 0.13733085],
       [0.97561494, 0.02438506],
       ...,
       [0.92741973, 0.07258027],
       [0.96528341, 0.03471659],
       [0.85394154, 0.14605846]])

In [72]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from imblearn.over_sampling import RandomOverSampler
from imblearn.under_sampling import RandomUnderSampler
from imblearn.pipeline import Pipeline

# Выделение целевой переменной и признаков
y = app_train['TARGET']
X = app_train.drop(['TARGET', 'SK_ID_CURR'], axis=1)

# Предобработка данных
X = pd.get_dummies(X, dummy_na=True)

# Разделение данных на обучающую и тестовую выборки
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Масштабирование признаков
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Балансировка классов
over_sampler = RandomOverSampler(sampling_strategy=0.5, random_state=42)
under_sampler = RandomUnderSampler(sampling_strategy=0.5, random_state=42)
steps = [('o', over_sampler), ('u', under_sampler)]
pipeline = Pipeline(steps=steps)
X_train, y_train = pipeline.fit_resample(X_train, y_train)

# Создание и обучение модели логистической регрессии
lr = LogisticRegression(random_state=42, max_iter=1000)
lr.fit(X_train, y_train)

# Оценка качества модели
y_pred = lr.predict(X_test)
score = lr.score(X_test, y_test)
print(f"Accuracy: {score:.2f}")



Accuracy: 0.84


In [73]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.impute import SimpleImputer

# Уберем таргет из тренировочных данных
if 'TARGET' in app_train:
    train = app_train.drop(labels = ['TARGET'], axis=1)
else:
    train = app_train.copy()
features = list(train.columns)

# копируем тестовые данные
test = app_test.copy()

# заполним недостающее по медиане
imputer = SimpleImputer(strategy = 'median')

# Нормализация
scaler = MinMaxScaler(feature_range = (0, 1))

# заполнение тренировочной выборки
imputer.fit(train)

# Трансофрмация тренировочной и тестовой выборок
train = imputer.transform(train)
test = imputer.transform(app_test)

# то же самое с нормализацией
scaler.fit(train)
train = scaler.transform(train)
test = scaler.transform(test)

print('Формат тренировочной выборки: ', train.shape)
print('Формат тестовой выборки: ', test.shape)

Формат тренировочной выборки:  (307510, 73)
Формат тестовой выборки:  (48744, 73)


In [74]:
#сохраним лейблы, их же нет в тестовой выборке и при выравнивании они потеряются. 
train_labels = app_train['TARGET']


In [75]:
from sklearn.linear_model import LogisticRegression

log_reg = LogisticRegression(C = 0.0001)

# Тренируем модель
log_reg.fit(train, train_labels)

LogisticRegression(C=0.0001)

In [76]:
log_reg_pred = log_reg.predict_proba(test)[:, 1]

In [77]:
submit = app_test[['SK_ID_CURR']]
submit['TARGET'] = log_reg_pred

submit.head()

/tmp/ipykernel_34/3970473317.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  submit['TARGET'] = log_reg_pred


SK_ID_CURR    TARGET
0      100001  0.069575
1      100005  0.094681
2      100013  0.060506
3      100028  0.068598
4      100038  0.093596

In [78]:
from sklearn.metrics import roc_auc_score

roc_auc = roc_auc_score(y_test, y_pred)
print(f'ROC AUC: {roc_auc:.4f}')

ROC AUC: 0.6330


In [91]:
def protected_division(x1, x2):
    if x2 == 0:
        return 1  # Защита от деления на ноль
    else:
        return x1 / x2

def protected_sqrt(x):
    if x < 0:
        return 0  # Защита от извлечения квадратного корня из отрицательного числа
    else:
        return np.sqrt(x)

def protected_log(x):
    if x <= 0:
        return 0  # Защита от логарифма от неположительного числа или нуля
    else:
        return np.log(x)


In [89]:
import numpy as np
import pandas as pd
from deap import creator, base, tools, gp
# Определение функций и операций для генерации новых признаков
pset = gp.PrimitiveSet("MAIN", arity=2)
pset.addPrimitive(np.add, arity=2)
pset.addPrimitive(np.subtract, arity=2)
pset.addPrimitive(np.multiply, arity=2)
pset.addPrimitive(np.maximum, arity=2)
pset.addPrimitive(np.minimum, arity=2)
pset.addPrimitive(protected_division, arity=2)
pset.addPrimitive(protected_sqrt, arity=1)
pset.addPrimitive(protected_log, arity=1)
pset.addPrimitive(np.sin, arity=1)
pset.addPrimitive(np.cos, arity=1)
pset.addTerminal(0)
pset.addTerminal(1)

In [92]:
# Создание класса для управления эволюцией
creator.create("FitnessMax", base.Fitness, weights=(1.0,))
creator.create("Individual", gp.PrimitiveTree, fitness=creator.FitnessMax)

# Инициализация пакета инструментов
toolbox = base.Toolbox()

# Определение функций и операций, которые могут быть использованы для создания новых признаков
toolbox.register("expr", gp.genHalfAndHalf, pset=pset, min_=1, max_=3)
toolbox.register("individual", tools.initIterate, creator.Individual, toolbox.expr)
toolbox.register("population", tools.initRepeat, list, toolbox.individual)

# Определение операторов мутации, скрещивания и оценки фитнеса
toolbox.register("mate", gp.cxOnePoint)
toolbox.register("mutate", gp.mutUniform, expr=toolbox.expr, pset=pset)
toolbox.register("evaluate", evaluate_fitness)
toolbox.register("select", tools.selTournament, tournsize=3)

/opt/conda/lib/python3.10/site-packages/deap/creator.py:138: RuntimeWarning: A class named 'FitnessMax' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "
/opt/conda/lib/python3.10/site-packages/deap/creator.py:138: RuntimeWarning: A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "


In [103]:
# Определение функции преобразования ГП структуры в вектор признаков
def transform_gp_structure(individual, X):
    expr = gp.compile(individual, pset)
    return np.array([expr(*row) for row in X])

# Определение функции оценки фитнеса (ваша собственная функция)
def evaluate_fitness(individual):
    # Вычислите значения признаков на основе individual
    X_train_gp = transform_gp_structure(individual, X_train)  # Вычисление новых признаков на обучающей выборке
    rf_model_gp.fit(X_train_gp, y_train)  # Обучение модели случайного леса с новыми признаками
    X_test_gp = transform_gp_structure(individual, X_test)  # Вычисление новых признаков на тестовой выборке
    y_pred_gp = rf_model_gp.predict_proba(X_test_gp)[:, 1]  # Прогнозирование на тестовой выборке с новыми признаками
    auc_gp = roc_auc_score(y_test, y_pred_gp)  # Оценка фитнеса (AUC-ROC)
    return auc_gp,

In [104]:
pop_size = 100  # Размер популяции
num_generations = 50  # Количество поколений

# Создание начальной популяции
population = toolbox.population(n=pop_size)

# Основной цикл эволюции
for generation in range(num_generations):
    # Оценка фитнеса
    fitnesses = map(evaluate_fitness, population)
    for individual, fitness in zip(population, fitnesses):
        individual.fitness.values = fitness

    # Выбор следующего поколения
    offspring = toolbox.select(population, len(population))

    # Клонирование выбранных индивидуумов
    offspring = list(map(toolbox.clone, offspring))

    # Применение операторов скрещивания и мутации
    for child1, child2 in zip(offspring[::2], offspring[1::2]):
        if random.random() < crossover_prob:
            toolbox.mate(child1, child2)
            del child1.fitness.values
            del child2.fitness.values

    for mutant in offspring:
        if random.random() < mutation_prob:
            toolbox.mutate(mutant)
            del mutant.fitness.values

    # Замена старого поколения потомками
    population[:] = offspring

TypeError: <lambda>() takes 2 positional arguments but 72 were given